In [ ]:
from vllm import LLM, SamplingParams
import pandas as pd
import numpy as np
import torch.nn.functional as F
import torch
from transformers import AutoTokenizer
from transformers import AutoModelForCausalLM
import re
import os
#os.environ["CUDA_VISIBLE_DEVICES"]="1"


In [ ]:
llama = LLM(model='hugging-quants/Meta-Llama-3.1-70B-Instruct-AWQ-INT4', tensor_parallel_size = 2, download_dir = "../meta_ai/", gpu_memory_utilization=0.80, max_model_len=10000)

In [ ]:
def generate_synthetic_clinical_notes(num_reports, llama_model):

    tokenizer = llama_model.get_tokenizer()
    prompts = []
    cancer_types = np.random.choice(['breast', 'non-small cell lung', 'small cell lung', 'colorectal', 'pancreatic', 'urothelial', 'prostate', 'gastric', 'esophageal', 'thymoma', 'thymic carcinoma', 'adrenal', 'ovarian', 'endometrial', 'melanoma', 'renal cell', 'sarcoma', 'head and neck', 'Hodgkin lymphoma', 'Non-Hodgkin lymphoma', 'myeloma', 'acute myeloid leukemia', 'chronic myeloid leukemia', 'acute lymphoblastic leukemia', 'chronic lymphocytic leukemia/lymphoma', 'primary brain tumor'], size=num_reports) 

    for i in range(num_reports):
        messages = [
            {'role':'system', 'content': """Your job is to generate synthetic oncologist clinical progress notes for hypothetical patients with cancer.
            You know all there is to know about cancer and its treatments, so be detailed.           
        """},      
              
            {'role':'user', 'content': """Imagine a patient with cancer. 
            The cancer type is""" + cancer_types[i] + "." + """
            The patient might have any stage of disease. Use everything you know about cancer, including biomarkers, epidemiology, and heterogeneity in disease presentations.
            The note might correspond to any point along the disease trajectory, from initial diagnosis to curative intent treatment to palliative intent treatment.
            The note should include a chief complaint, oncologic history including prior treatments, past medical history/comorbidities, current subjective clinical status and physical exam including vital signs and ECOG performance status, laboratory values, radiology excerpts, and an assessment and plan.
            The note should should be approximately two pages long. It will not be used for clinical care, so do not include disclaimers."""}
        ]
    
        prompts.append(tokenizer.apply_chat_template(conversation=messages, add_generation_prompt=True, tokenize=False))
    

    
    responses = llama_model.generate(
        prompts,   
        SamplingParams(
        temperature=1.0,
        top_p=0.9,
        max_tokens=4000,
        stop_token_ids=[tokenizer.eos_token_id, tokenizer.convert_tokens_to_ids("<|eot_id|>")],  # KEYPOINT HERE
    ))

    response_texts = [x.outputs[0].text for x in responses]


    return pd.DataFrame({'cancer_type':cancer_types, 'synthetic_clinical_note':response_texts})

In [ ]:
results = generate_synthetic_clinical_notes(10000, llama)

In [ ]:
results.to_csv('synthetic_clinical_notes.csv')